# Extract data from The National Map 3DEP WCS Service

In [1]:
import warnings
warnings.filterwarnings("ignore")

In [2]:
from owslib.wcs import WebCoverageService

endpoint = (
    "https://elevation.nationalmap.gov/arcgis/services/3DEPElevation/ImageServer/WCSServer"
    "?request=GetCapabilities"
    "&service=WCS"
)
wcs = WebCoverageService(endpoint, version="1.0.0", timeout=60)

In [3]:
for k, v in wcs.contents.items():
    print(k, v.title)

DEP3Elevation DEP3Elevation
DEP3Elevation_Hillshade Gray DEP3Elevation_Hillshade Gray
DEP3Elevation_Aspect Degrees DEP3Elevation_Aspect Degrees
DEP3Elevation_Aspect Map DEP3Elevation_Aspect Map
DEP3Elevation_Contour 25 DEP3Elevation_Contour 25
DEP3Elevation_Hillshade Elevation Tinted DEP3Elevation_Hillshade Elevation Tinted
DEP3Elevation_Height Ellipsoidal DEP3Elevation_Height Ellipsoidal
DEP3Elevation_GreyHillshade_elevationFill DEP3Elevation_GreyHillshade_elevationFill
DEP3Elevation_Hillshade Multidirectional DEP3Elevation_Hillshade Multidirectional
DEP3Elevation_Slope Map DEP3Elevation_Slope Map
DEP3Elevation_Slope Degrees DEP3Elevation_Slope Degrees
DEP3Elevation_Contour Smoothed 25 DEP3Elevation_Contour Smoothed 25


In [4]:
v = wcs["DEP3Elevation"]
print(v.title)
print(v.boundingBoxWGS84)
print(v.supportedFormats)

DEP3Elevation
(-179.99998854118687, -15.001663244822502, 179.99999272129153, 84.00167857213272)
['GeoTIFF', 'HDF']


In [5]:
# North Cascades Park
bbox = (-121.9, 48.7, -121.0, 49.3)
res = 0.0003
output = wcs.getCoverage(
    identifier="DEP3Elevation",
    bbox=bbox,
    crs="EPSG:4326",
    format="GeoTIFF",
    resx=res,
    resy=res
)

In [6]:
import xarray as xr
import hvplot.xarray
from io import BytesIO
from rasterio.io import MemoryFile

sio = BytesIO(output.read())  # Create an in-memory stream of the content

with MemoryFile(sio) as memfile:
    with memfile.open() as dataset:
        da = xr.open_rasterio(dataset)[0].drop_vars("band")

In [11]:
da.shape

(2000, 3000)

In [7]:
da.hvplot.image(x="x", y="y", geo=True, rasterize=True, cmap="rainbow")

:DynamicMap   []
   :Image   [x,y]   (value)

In [8]:
from xrspatial import hillshade
da_hs = hillshade(da)

In [9]:
da_hs.hvplot.image(rasterize=True, geo=True, colormap="gray")

/srv/conda/envs/pangeo/lib/python3.7/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/srv/conda/envs/pangeo/lib/python3.7/site-packages/pyproj/crs/crs.py:280: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(projparams)


:DynamicMap   []
   :Image   [x,y]   (hillshade)